In [3]:
import os
import numpy as np
import pandas as pd

import geopandas as gpd
import ee, eemont
import geemap
import geemap.colormaps as geecm

import matplotlib.pyplot as plt
import cmocean

# 1. Initialization GEE

In [4]:
ee.Authenticate(force=True)
ee.Initialize()

Enter verification code:  4/1Ab_5qlmoQavgOVFywXJghvaH8P-dT-b-QipgZc7KDFvbPNrsypfF_CuePVo



Successfully saved authorization token.


# 2. Load GEE datasets + parameters

In [5]:
dem_glo30 = ee.ImageCollection("COPERNICUS/DEM/GLO30")

In [6]:
fc_lia = ee.FeatureCollection('users/aguerou/ice_and_life/carto_h1b/lia_shp/glaciers_1850_final_mars_2025') # demander les références
geom_lia = ee.Geometry.convexHull(fc_lia.geometry())

## 2.3 Parameters

### a) Indices parameters

In [7]:
# Time parameters
startYear = 1984
endYear = 2024

startMonth = 7
endMonth = 9

date_filter = ee.Filter.calendarRange(7, 9, 'month') \
    .And(ee.Filter.calendarRange(15, None, 'day_of_month')) \
    .And(ee.Filter.calendarRange(None, 15, 'day_of_month'))

#Cloud correction
cloudThresh = 0.4
cloudBuff = 1000
cloudCover = 50

#

SlopeThresh = 20 
AltitudeThresh = 1000


### b) Params vis



In [8]:
palette_diff = geecm.get_palette('RdBu', n_class=7)
palette_ndwi = geecm.get_palette('viridis', n_class=7)
palette_gbr = cmocean.cm.ice
palette_dem = cmocean.cm.solar
palette_slope = cmocean.cm.matter
visParams_diff = {'min': -2, 'max': 2, 'palette': palette_diff}
visParams_ndwi = {'min': 0.0, 'max': 0.5, 'palette': palette_ndwi}
visParams_gbr = {'min': 0, 'max': 10, 'palette': palette_gbr}
visParams_dem = {'min': 1000, 'max': 4000, 'palette': palette_dem}
visParams_slope = {'min': 20, 'max': 60, 'palette': palette_slope}

visGLACIER = {"min": 0, "max": 1, "palette": ["#808080", "#a6cee3"]}
visWATER = {"min": 0, "max": 1, "palette": ["#808080", "#1f78b4"]}
visVEGET = {"min": 0, "max": 1, "palette": ["#808080", "#33a02c"]}

Scale and projection

In [9]:
scale = 30 #Landsat 30m
projection = "EPSG:4326" #GEE le plus stable avec ce SRC

# I. Functions

Mask terrain

In [10]:
def removeValley(image):
    return image.updateMask(valley_mask)

In [11]:
def get_slope(image):
    return ee.Terrain.slope(image)

Clouds

In [12]:
#V2 with comments : à conserver car filtre plus opti que le filtre interne du module
def addCloud(image):
    # Sélectionner le bande TIR et appliquer une échelle d'unité (unitScale)
    TIR = image.select('TIR').unitScale(240, 270).rename('sTIR')
    
    # Sélectionner le bande SWIR2
    SWIR2 = image.select('SWIR2').rename('sSWIR2')
    
    # Ajouter les bandes sTIR et sSWIR2
    temp = TIR.addBands(SWIR2)
    
    # Ajouter la bande de différence normalisée NDCI
    temp2 = temp.addBands(temp.normalizedDifference(['sTIR', 'sSWIR2']).rename('NDCI'))
    
    # Ajouter une bande NDCIt qui est le seuil des nuages
    temp3 = temp2.addBands(temp2.select('NDCI').lte(cloudThresh).rename('NDCIt'))
    
    # Calculer le masque avec la transformation de distance
    mask = temp3.select('NDCIt') \
                .fastDistanceTransform(50, 'pixels', 'squared_euclidean') \
                .sqrt() \
                .multiply(ee.Image.pixelArea().sqrt()) \
                .gt(cloudBuff)
    
    # Appliquer le masque à l'image 
    return image.updateMask(mask)

Index + scaling factors

In [13]:
#ref calcul des indices : https://doi.org/10.1016/j.rse.2021.112862 (notamment GBR et cloud filter)

def addGBR(image):
    gbr = image.expression(
        'NIR / SWIR1', 
        {
            'NIR': image.select('NIR'),  # Référence à la bande NIR
            'SWIR1': image.select('SWIR1')  # Référence à la bande SWIR1
        }
    )
    return image.addBands(gbr.rename('GBR'))

Clip geometry to LIA

In [14]:
def clip_to_lia(image,geom):
    return image.clip(geom)

Get Median

In [15]:
# Liste des années
years = ee.List.sequence(startYear, endYear)

# Fonction de traitement pour chaque année à mettre en haut
def process_year(year):
    # Filtrer la collection LXtemp pour l'année donnée
    start_date = ee.Date.fromYMD(year, 1, 1)
    end_date = ee.Date.fromYMD(year, 12, 31)
    year_collection = LXtemp.filterDate(start_date, end_date)
    # Calculer la médiane pour chaque année (sur les 3 bandes)
    annual_median = year_collection.median() \
                         .addBands(ee.Image.constant(ee.Number(year)).toDouble().rename('year')) \
                         .set('year', year) \
                         .selfMask()
    
    return annual_median


# II. Terrain data / Timeseries Landsat

Terrain

In [16]:
dem = ee.ImageCollection(dem_glo30).filterBounds(fc_lia).select("DEM")
dem_mosaic = dem.mosaic().clip(fc_lia)
slope = dem.map(get_slope).mosaic().clip(fc_lia) \
#need to map on single image for slope function to work fine

slope_mask = slope.lt(SlopeThresh)
valley_mask = dem_mosaic.gt(AltitudeThresh)

In [17]:
ee.Filter.calendarRange?

Signature:
ee.Filter.calendarRange(
    start: '_arg_types.Integer',
    end: 'Optional[_arg_types.Integer]' = None,
    field: 'Optional[_arg_types.String]' = None,
) -> 'Filter'
Docstring:
Returns a filter that passes if a timestamp is in a range.

Returns a filter that passes if the object's timestamp falls within the
given range of a calendar field.

The `month`, `day_of_year`, `day_of_month`, and `day_of_week` are 1-based.
Times are assumed to be in UTC. Weeks are assumed to begin on Monday as day
1. If `end` < `start` then this tests for `value` >= `start` OR `value` <=
`end`, to allow for wrapping.

Args:
  start: The start of the desired calendar field, inclusive.
  end: The end of the desired calendar field, inclusive. Defaults to the
    same value as start.
  field: The calendar field to filter over. Options are: `year`, `month`,
    `hour`, `minute`, `day_of_year`, `day_of_month`, and `day_of_week`.
File:      c:\users\ronir\anaconda3\envs\gee\lib\site-packages\ee\filter.py

Landsat

In [18]:
#ajouter les bandes correspondantes # virer Qa pixel
L5 = ee.ImageCollection("LANDSAT/LT05/C02/T1_L2") \
            .filter(ee.Filter.calendarRange(startMonth, endMonth,'month')) \
            .filterBounds(fc_lia) \
            .filterMetadata("CLOUD_COVER", "less_than", cloudCover) \
            .scaleAndOffset() \
            .map(lambda image: clip_to_lia(image,fc_lia)) \
            .spectralIndices(["NDWI","NDVI","NDSI","BITM"]) \
            .select(['SR_B1','SR_B2', 'SR_B3', 'SR_B4', 'SR_B5','SR_B7','ST_B6',"NDWI","NDVI","NDSI","BITM"], \
                    ['BLUE','GREEN', 'RED', 'NIR', 'SWIR1','SWIR2','TIR',"NDWI","NDVI","NDSI","BITM"])

L7 = ee.ImageCollection("LANDSAT/LE07/C02/T1_L2") \
            .filter(ee.Filter.calendarRange(startMonth, endMonth,'month')) \
            .filterBounds(fc_lia) \
            .filterMetadata('CLOUD_COVER', 'less_than', cloudCover) \
            .scaleAndOffset() \
            .map(lambda image: clip_to_lia(image,fc_lia)) \
            .spectralIndices(["NDWI","NDVI","NDSI","BITM"]) \
            .select(['SR_B1','SR_B2', 'SR_B3', 'SR_B4', 'SR_B5','SR_B7','ST_B6',"NDWI","NDVI","NDSI","BITM"],['BLUE','GREEN', 'RED', 'NIR', 'SWIR1','SWIR2','TIR',"NDWI","NDVI","NDSI","BITM"])

L8 = ee.ImageCollection("LANDSAT/LC08/C02/T1_L2") \
            .filter(ee.Filter.calendarRange(startMonth, endMonth,'month')) \
            .filterBounds(fc_lia) \
            .filterMetadata('CLOUD_COVER', 'less_than', cloudCover) \
            .scaleAndOffset() \
            .map(lambda image: clip_to_lia(image,fc_lia)) \
            .spectralIndices(["NDWI","NDVI","NDSI","BITM"]) \
            .select(['SR_B2','SR_B3', 'SR_B4', 'SR_B5', 'SR_B6','SR_B7','ST_B10',"NDWI","NDVI","NDSI","BITM"], \
                    ['BLUE','GREEN', 'RED', 'NIR', 'SWIR1','SWIR2','TIR',"NDWI","NDVI","NDSI","BITM"])

In [20]:
L8=L8.scaleAndOffset()
L8

In [19]:
L5_filtered=L5.filter(ee.Filter.dayOfYear(196, 258))
L7_filtered=L7.filter(ee.Filter.dayOfYear(196, 258))
L8_filtered=L8.filter(ee.Filter.dayOfYear(196, 258))


In [20]:
LXtemp = L5_filtered.merge(L7_filtered).merge(L8_filtered) \
                .map(addCloud) \
                .map(addGBR)  

In [21]:
annualCollection = ee.ImageCollection(years.map(process_year))

In [22]:
# Inspecter la collection annuelle
# print('Nombre d\'images dans la collection :', annualCollection.size().getInfo())

# # Obtenir le nom des bandes des images
# sample_image = annualCollection.first()  # Prendre la première image de la collection
# bands = sample_image.bandNames().getInfo()
# print('Bandes de l\'image :', bands)
# annualCollection


In [23]:
# annualCollection.limit(1)

In [25]:
#Préparation de l'export de l'Image Collection
List=['Landsat_index_1984',
 'Landsat_index_1985',
 'Landsat_index_1986',
 'Landsat_index_1987',
 'Landsat_index_1988',
 'Landsat_index_1989',
 'Landsat_index_1990',
 'Landsat_index_1991',
 'Landsat_index_1992',
 'Landsat_index_1993',
 'Landsat_index_1994',
 'Landsat_index_1995',
 'Landsat_index_1996',
 'Landsat_index_1997',
 'Landsat_index_1998',
 'Landsat_index_1999',
 'Landsat_index_2000',
 'Landsat_index_2001',
 'Landsat_index_2002',
 'Landsat_index_2003',
 'Landsat_index_2004',
 'Landsat_index_2005',
 'Landsat_index_2006',
 'Landsat_index_2007',
 'Landsat_index_2008',
 'Landsat_index_2009',
 'Landsat_index_2010',
 'Landsat_index_2011',
 'Landsat_index_2012',
 'Landsat_index_2013',
 'Landsat_index_2014',
 'Landsat_index_2015',
 'Landsat_index_2016',
 'Landsat_index_2017',
 'Landsat_index_2018',
 'Landsat_index_2019',
 'Landsat_index_2020',
 'Landsat_index_2021',
 'Landsat_index_2022',
 'Landsat_index_2023',
 'Landsat_index_2024']


In [31]:
# Loop through each image in the annualCollection and export it
for i in range(annualCollection.size().getInfo()):
    image = ee.Image(annualCollection.toList(annualCollection.size()).get(i))
    
    
    # Export the image
    geemap.ee_export_image_to_asset(
        image=image,
        description=None,
        assetId=f'projects/ee-roniritzganem/assets/stage_carrtel_2025/landsat_annual_median_index/Landsat_{1983+i}',
        region=geom_lia,
        scale=scale,
        maxPixels=1e13,
        crs=projection
    )

In [26]:
# Exporter la collection d'images vers un Asset GEE
geemap.ee_export_image_collection_to_asset(
    annualCollection,
    descriptions = List,
    assetIds='projects/ee-roniritzganem/assets/stage_carrtel_2025/landsat_annual_median_index',
    dimensions=None,
    region=geom_lia,
    scale=scale,
    maxPixels=2e9,
    crs=projection)

Total number of images: 41

Name "projects/earthengine-legacy/assets/projects/891219672665/assets/stage_carrtel_2025//" is invalid. Each segment must contain only the following characters: a..z, A..Z, 0..9, "_" or "-". Each segment must be at least 1 character long and at most 100 characters long.


In [39]:
# asset_base_path = 'projects/ee-roniritzganem/assets/stage_carrtel_2025/annual_median_index'
# image_list = annualCollection.toList(annualCollection.size())
# asset_ids = [
#     f"{asset_base_path}/image_{i}" for i in range(annualCollection.size().getInfo())
# ]
# first_image = ee.Image(annualCollection.toList(annualCollection.size()).get(0))
# first_image

# geemap.ee_export_image_to_asset(
#     image=first_image,
#     description='export_first_image',
#     assetId='projects/ee-roniritzganem/assets/stage_carrtel_2025/first_image',
#     region=geom_lia,
#     scale=scale,
#     maxPixels=1e13,
#     crs=projection
# )

# Ensuite, exporter la collection
# geemap.ee_export_image_to_asset(
#     annualCollection,
#     assetIds=asset_ids,
#     dimensions=None,
#     region=geom_lia,
#     scale=scale,
#     maxPixels=2e9,
#     crs=projection
# )

In [ ]:
# Exporter la collection d'images vers un Asset GEE
# geemap.ee_export_image_collection_to_drive(
#     annualCollection,
#     folder='Stage_Carrtel_2025',
#     fileNamePrefix='Median_AnnualCollection_index',
#     dimensions=None,
#     region=geom_lia,
#     scale=scale,
#     maxPixels=2e9,
#     crs=projection)